# Ноутбук для тюнинга модели

Этот ноутбук предназначен для подбора гиперпараметров модели, анализа влияния отдельных компонент архитектуры и выбора оптимальной конфигурации для последующих экспериментов. Здесь выполняются эксперименты по поиску параметров, сравнение различных режимов обучения и анализ качества модели на валидации.


In [ ]:
import os
import pandas as pd
import numpy as np
from pathlib import Path
from tqdm import tqdm

from uplift import *

2025-09-29 20:35:53.528843: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-09-29 20:35:53.542101: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1759167353.552749    5578 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1759167353.556225    5578 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1759167353.565915    5578 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

In [3]:
evaluator = Evaluator()
DATASETS = ['CO', 'CP']
mesuares = ['CPrec_10', 'CPrec_100', 'CDCG', 'CDCG_100']
answers = []

In [4]:
base_rng = np.random.default_rng(12345)
seeds = base_rng.integers(low=0, high=10**9, size=5)
seeds # для нескольких запусков модели

array([699215031, 227336022, 788646988, 316758339, 204176893])

# PropCare tune

In [ ]:
import optuna
import pandas as pd
import os
from pathlib import Path
import warnings
warnings.filterwarnings("ignore", category=UserWarning, module="optuna")

def tune_propcare_optuna(dataset_name="CO", path_to_data="./", min_metric='kld', n_trials=20, result_path="results/propcare_optuna.csv"):
    train_df, vali_df, _, num_users, num_items, item_popularity = get_dataset(dataset_name, path_to_data)

    def objective(trial):
        class Args:
            dimension = trial.suggest_int("dimension", 64, 300)
            embedding_layer_units = trial.suggest_categorical(
                "embedding_layer_units",
                [
                    [128],
                    [256, 128],
                    [256, 128, 64],
                    [512, 256],
                    [512, 256, 128],
                    [1024, 512, 256]
                ]
            )

            estimator_layer_units = trial.suggest_categorical(
                "estimator_layer_units",
                [
                    [64],
                    [64, 32],
                    [64, 32, 16],
                    [64, 32, 16, 8],
                    [128, 64],
                    [128, 64, 32],
                    [128, 64, 32, 16]
                ]
            )
            lambda_1 = trial.suggest_float("lambda_1", 0.01, 10.0, log=True)
            lr = trial.suggest_float("lr", 1e-4, 1e-2, log=True)

        args = Args()

        print(f"\n📌 Trial #{trial.number} Params:")
        print(f'dimension {args.dimension}; embedding_layer_units {args.embedding_layer_units}; estimator_layer_units {args.estimator_layer_units}; lambda_1 {args.lambda_1}; lr {args.lr};')

        model = PropCare(
            num_users=num_users,
            num_items=num_items,
            args=args,
            item_popularity=item_popularity,
            device="cuda"
        )

        model.fit(train_df, vali_df, batch_size=4096, epochs=25)
        val_metrics = model.get_metrics(vali_df)

        score = val_metrics.get(min_metric, 0.0)
        trial.set_user_attr("val_metrics", val_metrics)
        trial.set_user_attr("params", args.__dict__)

        return score

    study = optuna.create_study(direction="minimize")
    optuna.logging.set_verbosity(optuna.logging.WARNING)
    study.optimize(objective, n_trials=n_trials, show_progress_bar=True)

    rows = []
    for trial in study.trials:
        row = {
            "trial_id": trial.number,
            "dataset": dataset_name,
            "value": trial.value
        }
        row.update(trial.params)
        row.update(trial.user_attrs.get("val_metrics", {}))
        rows.append(row)

    df_results = pd.DataFrame(rows)
    Path(result_path).parent.mkdir(parents=True, exist_ok=True)

    if os.path.exists(result_path):
        df_old = pd.read_csv(result_path)
        df_results = pd.concat([df_old, df_results], ignore_index=True)

    df_results.to_csv(result_path, index=False)
    print(f"Сохранены все {len(rows)} трейлы в {result_path}")


In [ ]:
for dataset in DATASETS:
    tune_propcare_optuna(
        dataset_name=dataset,
        path_to_data="./",
        n_trials=25,
        result_path=f"results/propcare_optuna_{dataset}.csv"
    )


  0%|          | 0/25 [00:00<?, ?it/s]


📌 Trial #0 Params:
dimension 78; embedding_layer_units [256, 128]; estimator_layer_units [128, 64]; lambda_1 0.11722298981998686; lr 0.00014163675891169927;


Epoch 0: 100%|██████████████████████████| 1949/1949 [00:13<00:00, 145.97batch/s]


Epoch 0: train loss = 0.4862 | val corr = {'kld': np.float64(0.6912929065642216), 'tau': np.float64(0.019732516689314406), 'f1': 0.22847095698728995}


Epoch 1: 100%|██████████████████████████| 1949/1949 [00:12<00:00, 160.49batch/s]


...

Epoch 23: train loss = 0.4270 | val corr = {'kld': np.float64(1.0625753406729264), 'tau': np.float64(0.35056337109770896), 'f1': 0.5437228298362266}


Epoch 24: 100%|█████████████████████████| 1887/1887 [00:13<00:00, 142.09batch/s]


Epoch 24: train loss = 0.4261 | val corr = {'kld': np.float64(1.074232669494388), 'tau': np.float64(0.3412757659943337), 'f1': 0.5426659266013447}


Best trial: 6. Best value: 0.741097: 100%|██████████| 25/25 [3:05:38<00:00, 445.52s/it]

Сохранены все 25 трейлы в results/propcare_optuna_CP.csv


In [38]:
df = pd.read_csv("results/propcare_optuna_CO.csv")
df.sort_values(by='tau', ascending=False)

trial_id dataset     value  dimension embedding_layer_units  \
10         8      CO  0.814314        195       [512, 256, 128]   
25        23      CO  0.809462        180       [512, 256, 128]   
5          3      CO  0.544888        198       [512, 256, 128]   
12        10      CO  0.940575        228            [512, 256]   
8          6      CO  1.889225        266        [256, 128, 64]   
18        16      CO  3.258022        116        [256, 128, 64]   
19        17      CO  0.766541        170       [512, 256, 128]   
22        20      CO  0.728797        253        [256, 128, 64]   
9          7      CO  0.674631        185       [512, 256, 128]   
23        21      CO  0.687554        226       [512, 256, 128]   
11         9      CO  0.726226        135      [1024, 512, 256]   
3          1      CO  0.755896        279                 [128]   
20        18      CO  0.686792        230       [512, 256, 128]   
6          4      CO  0.692121        242       [512, 256, 128]   
24        22      CO  0.694536        217       [512, 256, 128]   
15        13      CO  0.741281        211            [512, 256]   
13        11      CO  0.705576        188       [512, 256, 128]   
14        12      CO  0.706482        139            [256, 128]   
2          0      CO  0.688335         78            [256, 128]   
26        24      CO  0.845552        235       [512, 256, 128]   
7          5      CO  3.561267        161       [512, 256, 128]   
1          1      CO  0.008351         80            (256, 128)   
16        14      CO  3.157061        158                 [128]   
17        15      CO  2.265929        299      [1024, 512, 256]   
0          0      CO -0.008563        292                (128,)   
4          2      CO  1.363565         88       [512, 256, 128]   
27         0      CO  1.759491        200        [256, 128, 64]   
21        19      CO  1.566852        205       [512, 256, 128]   

   estimator_layer_units  lambda_1        lr       kld       tau        f1  
10             [128, 64]  0.491928  0.001192  0.814314  0.206361  0.387963  
25             [128, 64]  0.526705  0.000666  0.809462  0.192471  0.382311  
5              [128, 64]  7.161394  0.007882  0.544888  0.189961  0.355251  
12          [64, 32, 16]  0.010801  0.009002  0.940575  0.153598  0.272627  
8        [64, 32, 16, 8]  1.210917  0.000491  1.889225  0.138828  0.367926  
18          [64, 32, 16]  1.429522  0.000800  3.258022  0.136647  0.415559  
19                  [64]  0.030198  0.003001  0.766541  0.126849  0.298726  
22              [64, 32]  0.042073  0.001468  0.728797  0.102142  0.285205  
9               [64, 32]  0.129230  0.000488  0.674631  0.086156  0.286626  
23             [128, 64]  0.296160  0.000255  0.687554  0.085570  0.301894  
11     [128, 64, 32, 16]  0.543970  0.000220  0.726226  0.079460  0.333273  
3          [128, 64, 32]  0.010448  0.001508  0.755896  0.073982  0.248573  
20             [128, 64]  0.280877  0.000266  0.686792  0.072155  0.309096  
6        [64, 32, 16, 8]  4.064001  0.003452  0.692121  0.065462  0.315896  
24             [128, 64]  0.198149  0.000271  0.694536  0.062175  0.288494  
15              [64, 32]  0.042565  0.000835  0.741281  0.046731  0.238298  
13              [64, 32]  0.099988  0.000446  0.705576  0.039077  0.269177  
14              [64, 32]  0.089399  0.000390  0.706482  0.026430  0.224795  
2              [128, 64]  0.117223  0.000142  0.688335  0.026308  0.228546  
26             [128, 64]  0.696374  0.000111  0.845552  0.023534  0.309932  
7              [128, 64]  2.752830  0.000142  3.561267  0.021492  0.329987  
1        (64, 32, 16, 8)  0.020429  0.006111  0.723785  0.008351  0.213706  
16         [128, 64, 32]  1.281058  0.002126  3.157061  0.004955  0.358295  
17     [128, 64, 32, 16]  0.205983  0.008651  2.265929 -0.006731  0.334273  
0        (64, 32, 16, 8)  0.600664  0.001269  0.737740 -0.008563  0.230305  
4                   [64]  6.740053  0.004449  1.363565 -0.

### 🔍 Лучшие параметры модели по результатам анализа

После проведения анализа полученных результатов, были выявлены следующие оптимальные значения гиперпараметров:

- `dimension` — **200**  
  Размерность эмбеддингов, обеспечивающая наилучший баланс между точностью и обобщающей способностью модели.

- `embedding_layer_units` — **[512, 256]**  
  Архитектура слоев эмбеддинга, обеспечивающая глубокое представление входных данных.

- `estimator_layer_units` — **[64, 32, 16]**  
  Конфигурация слоев оценочной (предсказывающей) части модели, эффективно обучающейся на скрытых представлениях.

- `lambda_1` — **0.1**  
  Коэффициент регуляризации на веса модели, контролирующий переобучение.

- `lambda_2` — **1e-4**  
  Коэффициент регуляризации на веса модели, контролирующий переобучение.

- `lr` (learning rate) — **0.0085**  
  Оптимальная скорость обучения, обеспечивающая стабильную и быструю сходимость.

> ⚙️ Эти параметры демонстрировали наилучшие результаты по выбранным метрикам качества.


In [ ]:
for dataset in DATASETS:
    train_df, vali_df, test_df, num_users, num_items, item_popularity = get_dataset(dataset, "./")

    for i in range(len(seeds)):
        
        class Args:
            dimension = 200
            embedding_layer_units = [512, 256]
            estimator_layer_units = [64, 32, 16]
            lambda_1 = 0.1
            lambda_2 = 1e-4
            lr = 0.0085
            seed = seeds[i]
        
        args = Args()

        model = PropCare(
            num_users=num_users,
            num_items=num_items,
            args=args,
            item_popularity=item_popularity,
            device="cuda"
        )

        model.fit(train_df, vali_df, epochs=30, batch_size=4096)

        model.save_model(dir_path=f"saved_models/propcare/best_{dataset}2", model_name=f"model_{i+1}")


Epoch 0: 100%|██████████████████████████| 1949/1949 [00:16<00:00, 118.19batch/s]


Epoch 0: train loss = 0.3562 | val corr = {'kld': np.float64(0.7061163161169336), 'tau': np.float64(0.03806743412220206), 'f1': 0.24011391175346242}


Epoch 1: 100%|██████████████████████████| 1949/1949 [00:12<00:00, 152.98batch/s]


Epoch 1: train loss = 0.3067 | val corr = {'kld': np.float64(0.7196552603202534), 'tau': np.float64(0.0712233020168224), 'f1': 0.26444254886180985}


Epoch 2: 100%|██████████████████████████| 1949/1949 [00:15<00:00, 129.16batch/s]


...

Epoch 27: train loss = 0.2586 | val corr = {'kld': np.float64(0.8934932258836634), 'tau': np.float64(0.19099852042129545), 'f1': 0.3856902745278977}


Epoch 28: 100%|█████████████████████████| 1949/1949 [00:12<00:00, 152.11batch/s]


Epoch 28: train loss = 0.2581 | val corr = {'kld': np.float64(0.8938721742948625), 'tau': np.float64(0.18426347544912625), 'f1': 0.3855343927579204}


Epoch 29: 100%|█████████████████████████| 1949/1949 [00:14<00:00, 130.14batch/s]


Epoch 29: train loss = 0.2576 | val corr = {'kld': np.float64(0.8940319006866007), 'tau': np.float64(0.17728925661593498), 'f1': 0.38589624393871474}
Model saved to: saved_models/propcare/best_CO2/model_5


# DLCE tune

In [ ]:
import optuna
import pandas as pd
import os
from pathlib import Path

def tune_dlce_optuna(dataset_name="CO", path_to_data="./", min_metric='CDCG', n_trials=20,
                    result_path="results/dlce_res.csv", prop_mode='original', propcare_ablation_mode=None):
    train_df, vali_df, _, num_users, num_items, _ = get_dataset(dataset_name, path_to_data)

    if prop_mode == 'original':
        pass
    elif prop_mode == 'random':
        rd = RandomBase(num_users, num_items)
        rd.fit(train_df)
        train_df['propensity'] = rd.predict(train_df)
        vali_df['propensity'] = rd.predict(vali_df)

        train_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), train_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
        vali_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), vali_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
    elif prop_mode == 'popular':
        pop = PopularBase(num_users, num_items)
        pop.fit(train_df)
        train_df['propensity'] = pop.predict(train_df)
        vali_df['propensity'] = pop.predict(vali_df)

        train_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), train_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
        vali_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), vali_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
    elif prop_mode == 'propcare':
        if propcare_ablation_mode is not None:
            propcare = PropCare.load_model(dir_path=f"saved_models/propcare/ablation", model_name=f"model_CP_{propcare_ablation_mode}", device='cuda')
        else:
            propcare = PropCare.load_model(dir_path=f"saved_models/propcare/best_{dataset_name}", model_name=f"model_1", device='cuda')
        
        train_df['propensity'] = propcare.predict(train_df)
        vali_df['propensity'] = propcare.predict(vali_df)

        train_df['treated'] =  propcare.predict_z(train_df)
        vali_df['treated'] = propcare.predict_z(vali_df)
    else:
        raise NotImplementedError


    def objective(trial):

        params = {
            "dim_factor": trial.suggest_int("dim_factor", 80, 256),  # обе модели попали в этот диапазон
            "metric": trial.suggest_categorical("metric", ["upper_bound_log", "upper_bound_sigmoid", "upper_bound_hinge"]),
            "learn_rate": trial.suggest_float("learn_rate", 3e-4, 3e-2, log=True),  # оба значения были около 0.009
            "reg_factor": trial.suggest_float("reg_factor", 1e-5, 5e-3, log=True),  # была от 1e-4 до 2e-3
            "reg_bias": trial.suggest_float("reg_bias", 1e-5, 1e-3, log=True),  # оба около 1e-4 — 6e-4
            "omega": trial.suggest_float("omega", 0.01, 0.2),  # значения около 0.07–0.19
            "xT": trial.suggest_float("xT", 0.01, 0.06),  # около 0.04–0.05
            "xC": trial.suggest_float("xC", 0.001, 0.06),
            "tau_mode": trial.suggest_categorical("tau_mode", ["ips"]),
            "with_bias": trial.suggest_categorical("with_bias", [True, False]),
            "with_outcome": trial.suggest_categorical("with_outcome", [True]),
            "only_treated": trial.suggest_categorical("only_treated", [False]),
        }

        model = DLCE(
            num_users=num_users,
            num_items=num_items,
            device="cuda",
            **params
        )

        model.fit(train_df, vali_df, n_epochs=25, batch_size=512)
        val_metrics = model.get_metrics(vali_df)

        score = val_metrics.get(min_metric, 0.0)

        trial.set_user_attr("val_metrics", val_metrics)
        trial.set_user_attr("params", params)

        return -score  # minimization

    study = optuna.create_study(direction="minimize")
    optuna.logging.set_verbosity(optuna.logging.WARNING)
    study.optimize(objective, n_trials=n_trials, show_progress_bar=True)


    # Сохраняем ВСЕ трейлы
    rows = []
    for _, trial in enumerate(study.trials):
        row = {
            "trial_id": trial.number,
            "dataset": dataset_name,
            "value": -trial.value
        }
        row.update(trial.params)
        row.update(trial.user_attrs.get("val_metrics", {}))
        rows.append(row)

    df_results = pd.DataFrame(rows)

    Path(result_path).parent.mkdir(parents=True, exist_ok=True)

    # # Удаляем файл, если он уже есть
    # if os.path.exists(result_path):
    #     os.remove(result_path)

    # Проверяем, если файл уже существует — подгружаем старые трейлы
    if os.path.exists(result_path):
        df_old = pd.read_csv(result_path)
        df_results = pd.concat([df_old, df_results], ignore_index=True)

    df_results.to_csv(result_path, index=False)
    print(f"Сохранены все {len(rows)} трейлы в {result_path}")


/home/sever/miniconda/envs/casual10/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [16]:
for dataset in DATASETS:
    tune_dlce_optuna(
        dataset_name=dataset,
        min_metric='CDCG',
        path_to_data="./",
        n_trials=25,
        result_path=f"results/dlce_optuna_{dataset}.csv",
        prop_mode='original'
    )


  0%|          | 0/25 [00:00<?, ?it/s]

Epoch 1/25, Train Loss: 997.3879, Validation Metrics: {'CPrec_10': np.float64(0.005023819835426591), 'CPrec_100': np.float64(0.00519705500216544), 'CDCG_100': 0.10958881103151256, 'CDCG': 0.7148743381630946}


Epoch 2/25, Train Loss: 943.0142, Validation Metrics: {'CPrec_10': np.float64(0.006019922044174967), 'CPrec_100': np.float64(0.005751407535729753), 'CDCG_100': 0.12276461746023341, 'CDCG': 0.7258465464870936}


Epoch 3/25, Train Loss: 898.3043, Validation Metrics: {'CPrec_10': np.float64(0.007708964919878735), 'CPrec_100': np.float64(0.006730186227804244), 'CDCG_100': 0.14931264439280367, 'CDCG': 0.7436318848088908}


Epoch 4/25, Train Loss: 860.9833, Validation Metrics: {'CPrec_10': np.float64(0.012039844088349934), 'CPrec_100': np.float64(0.0074924209614551755), 'CDCG_100': 0.18523645675246117, 'CDCG': 0.7739063506570296}


...

Epoch 23/25, Train Loss: 181.5474, Validation Metrics: {'CPrec_10': np.float64(0.06851450844521438), 'CPrec_100': np.float64(0.03803378085751408), 'CDCG_100': 0.9162828422160677, 'CDCG': 1.202134842826465}


Epoch 24/25, Train Loss: 179.4793, Validation Metrics: {'CPrec_10': np.float64(0.07085318319618883), 'CPrec_100': np.float64(0.03838025119099177), 'CDCG_100': 0.927913905897724, 'CDCG': 1.2090182428077483}


Epoch 25/25, Train Loss: 178.5277, Validation Metrics: {'CPrec_10': np.float64(0.06760502381983542), 'CPrec_100': np.float64(0.038622780424426156), 'CDCG_100': 0.9319456433018749, 'CDCG': 1.2096931743340642}


Best trial: 1. Best value: -1.28601: 100%|██████████| 25/25 [1:24:37<00:00, 203.08s/it]

Сохранены все 25 трейлы в results/dlce_optuna_CP.csv


## Анализируем получившиеся результаты

In [49]:
df = pd.read_csv("results/dlce_optuna_CO.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.07]

trial_id dataset     value  dim_factor             metric  learn_rate  \
0          0      CO  1.141101         238    upper_bound_log    0.002393   
5          5      CO  1.142298          99  upper_bound_hinge    0.003152   
13        13      CO  1.110087         163    upper_bound_log    0.006312   
24        24      CO  1.107560         184    upper_bound_log    0.004556   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
0     0.000448  0.000010  0.032770  0.050826  0.013195      ips       True   
5     0.000763  0.000136  0.011696  0.016896  0.033103      ips       True   
13    0.000727  0.000010  0.051265  0.024584  0.036971      ips       True   
24    0.000788  0.000013  0.079034  0.019012  0.025876      ips       True   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
0           True         False  0.077523   0.021009  0.696778  1.141101  
5           True         False  0.072369   0.022633  0.705507  1.142298  
13          True         False  0.071156   0.021628  0.674256  1.110087  
24          True         False  0.070637   0.021460  0.672192  1.107560

In [50]:
df = pd.read_csv("results/dlce_optuna_CP.csv")
best_CP = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.07]

trial_id dataset     value  dim_factor             metric  learn_rate  \
1          1      CP  1.286011         223    upper_bound_log    0.008065   
4          4      CP  1.239192         198    upper_bound_log    0.004203   
12        12      CP  1.197767         218    upper_bound_log    0.021060   
15        15      CP  1.229128         256    upper_bound_log    0.015006   
17        17      CP  1.252903         231    upper_bound_log    0.010196   
18        18      CP  1.209131         228  upper_bound_hinge    0.012015   
22        22      CP  1.225678         213    upper_bound_log    0.005864   
23        23      CP  1.236074         238    upper_bound_log    0.009806   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
1     0.000389  0.000547  0.067456  0.039814  0.054311      ips       True   
4     0.000697  0.000495  0.154116  0.017937  0.011970      ips      False   
12    0.000722  0.000297  0.148315  0.025385  0.023593      ips       True   
15    0.000561  0.000724  0.197428  0.010433  0.047713      ips       True   
17    0.000178  0.000242  0.161293  0.040208  0.030183      ips      False   
18    0.000193  0.000192  0.174470  0.041682  0.032067      ips      False   
22    0.000289  0.000948  0.177714  0.038173  0.014899      ips      False   
23    0.001810  0.000480  0.158796  0.046161  0.001952      ips      False   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
1           True         False  0.085275   0.040927  1.036919  1.286011  
4           True         False  0.073019   0.039506  0.969875  1.239192  
12          True         False  0.075790   0.033837  0.860984  1.197767  
15          True         False  0.077523   0.036094  0.921690  1.229128  
17          True         False  0.079472   0.039428  0.986510  1.252903  
18          True         False  0.076527   0.036908  0.911057  1.209131  
22          True         False  0.077783   0.039671  0.964412  1.225678  
23          True         False  0.081161   0.036652  0.929566  1.236074

### Теперь 5 раз запустим лучшую модель для эксперементов с разными seed

In [58]:
for dataset in DATASETS:
    train_df, vali_df, test_df, num_users, num_items, _ = get_dataset(dataset, "./")

    df = pd.read_csv(f"results/dlce_optuna_{dataset}.csv")
    best_params = df.iloc[[df['CPrec_10'].idxmax()]].squeeze().to_dict()

    for i in range(len(seeds)):
        model = DLCE(
            num_users=num_users,
            num_items=num_items,
            dim_factor=int(best_params['dim_factor']),
            metric=best_params['metric'],
            learn_rate=best_params['learn_rate'],
            reg_factor=best_params['reg_factor'],
            reg_bias=best_params['reg_bias'],
            omega=best_params['omega'],
            xT=best_params['xT'],
            xC=best_params['xC'],
            tau_mode=best_params['tau_mode'],
            with_bias=bool(best_params['with_bias']),
            with_outcome=bool(best_params['with_outcome']),
            only_treated=bool(best_params['only_treated']),
            device='cuda',
            seed = seeds[i]
        )

        # Обучаем модель
        model.fit(train_df, vali_df, n_epochs=40, batch_size=512)

        model.save_model(dir_path=f"saved_models/dlce/best_{dataset}", model_name=f"model_{i+1}")


DLCE:   2%|▉                                     | 1/40 [00:09<06:16,  9.66s/it]

Epoch 1/40, Train Loss: 999.4240, Validation Metrics: {'CPrec_10': np.float64(0.005413598960588999), 'CPrec_100': np.float64(0.004898224339540927), 'CDCG_100': 0.10756261718657602, 'CDCG': 0.7165487303063738}


DLCE:   5%|█▉                                    | 2/40 [00:16<05:07,  8.10s/it]

Epoch 2/40, Train Loss: 944.2054, Validation Metrics: {'CPrec_10': np.float64(0.0071026418362927675), 'CPrec_100': np.float64(0.005478562148116067), 'CDCG_100': 0.12321567915769423, 'CDCG': 0.7296264688684526}


DLCE:   8%|██▊                                   | 3/40 [00:23<04:38,  7.52s/it]

...

DLCE:  95%|███████████████████████████████████▏ | 38/40 [05:06<00:16,  8.09s/it]

Epoch 38/40, Train Loss: 240.1736, Validation Metrics: {'CPrec_10': np.float64(0.08605456907752274), 'CPrec_100': np.float64(0.04126028583802512), 'CDCG_100': 1.0388273810204496, 'CDCG': 1.282548596516224}


DLCE:  98%|████████████████████████████████████ | 39/40 [05:14<00:08,  8.20s/it]

Epoch 39/40, Train Loss: 238.5770, Validation Metrics: {'CPrec_10': np.float64(0.0844521437851884), 'CPrec_100': np.float64(0.04123430056301429), 'CDCG_100': 1.0318801485577282, 'CDCG': 1.2762031532602687}


Epoch 40/40, Train Loss: 238.4267, Validation Metrics: {'CPrec_10': np.float64(0.09021221307925509), 'CPrec_100': np.float64(0.04129060199220442), 'CDCG_100': 1.054635815683716, 'CDCG': 1.2970062490457817}
Model saved to: saved_models/dlce/best_CP/model_5


# DLCE на остальных режимах 

In [5]:
for mode in ['random', 'popular', 'propcare']:
    for dataset in ['CO', 'CP']:
        tune_dlce_optuna(
            dataset_name=dataset,
            path_to_data="./",
            n_trials=25,
            result_path=f"results/dlce_on_{mode}_{dataset}.csv",
            prop_mode=mode
        )


[I 2025-09-14 17:36:59,647] A new study created in memory with name: no-name-26917987-72cb-497e-8660-557458d1abfa
  0%|          | 0/25 [00:00<?, ?it/s]

Epoch 1/25, Train Loss: 901.8478, Validation Metrics: {'CPrec_10': np.float64(0.00519705500216544), 'CPrec_100': np.float64(0.004763967085318319), 'CDCG_100': 0.10130911013608752, 'CDCG': 0.7070754342659421}


Epoch 2/25, Train Loss: 850.6750, Validation Metrics: {'CPrec_10': np.float64(0.0043308791684712), 'CPrec_100': np.float64(0.004452143785188393), 'CDCG_100': 0.09407441710432857, 'CDCG': 0.703749525978551}


Epoch 3/25, Train Loss: 807.3755, Validation Metrics: {'CPrec_10': np.float64(0.0034647033347769596), 'CPrec_100': np.float64(0.004395842355998268), 'CDCG_100': 0.09043389893459934, 'CDCG': 0.7002700452582389}


Epoch 4/25, Train Loss: 762.9497, Validation Metrics: {'CPrec_10': np.float64(0.0034213945430922477), 'CPrec_100': np.float64(0.004309224772628843), 'CDCG_100': 0.0884008727616637, 'CDCG': 0.6988302614578742}


...

Epoch 23/25, Train Loss: 1007.4974, Validation Metrics: {'CPrec_10': np.float64(0.0786920744911217), 'CPrec_100': np.float64(0.02848852317020355), 'CDCG_100': 0.8168338019791401, 'CDCG': 1.1850009667046104}


Epoch 24/25, Train Loss: 991.5641, Validation Metrics: {'CPrec_10': np.float64(0.08016457340840191), 'CPrec_100': np.float64(0.028670420095279342), 'CDCG_100': 0.8189005933546334, 'CDCG': 1.184447060511015}


Epoch 25/25, Train Loss: 977.0581, Validation Metrics: {'CPrec_10': np.float64(0.07947163274144652), 'CPrec_100': np.float64(0.029220441749675183), 'CDCG_100': 0.8402164043997136, 'CDCG': 1.1978981442682033}


Best trial: 24. Best value: -1.1979: 100%|██████████| 25/25 [1:19:17<00:00, 190.31s/it] 

Сохранены все 25 трейлы в results/dlce_on_propcare_CP.csv


## посмотрит на результаты при обучении на random

In [ ]:
import pandas as pd

df = pd.read_csv("results/dlce_on_random_CO.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.015]

trial_id dataset     value  dim_factor               metric  learn_rate  \
10        10      CO  0.764873          82  upper_bound_sigmoid    0.000598   
14        14      CO  0.789922         104  upper_bound_sigmoid    0.004279   
19        19      CO  0.767013         156  upper_bound_sigmoid    0.001126   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
10    0.000011  0.000166  0.018362  0.010482  0.001369      ips       True   
14    0.000086  0.000086  0.048428  0.028837  0.013143      ips       True   
19    0.000115  0.000015  0.083492  0.046221  0.006614      ips       True   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
10          True         False  0.015894   0.007510  0.192106  0.764873  
14          True         False  0.017280   0.011031  0.254004  0.789922  
19          True         False  0.016197   0.007544  0.193541  0.767013

In [25]:
df = pd.read_csv("results/dlce_on_random_CP.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.02]

trial_id dataset     value  dim_factor             metric  learn_rate  \
14        14      CP  0.827024         219  upper_bound_hinge    0.008704   
17        17      CP  0.789834         189    upper_bound_log    0.012056   
18        18      CP  0.784868         187    upper_bound_log    0.012775   
20        20      CP  0.795654         237    upper_bound_log    0.012393   
21        21      CP  0.795285         231    upper_bound_log    0.013217   
22        22      CP  0.811475         231    upper_bound_log    0.005056   
23        23      CP  0.817127         242    upper_bound_log    0.004976   
24        24      CP  0.813982         255    upper_bound_log    0.005052   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
14    0.000348  0.000019  0.046157  0.043357  0.051965      ips       True   
17    0.000067  0.000022  0.053958  0.042950  0.051954      ips       True   
18    0.000051  0.000160  0.070249  0.040505  0.038482      ips       True   
20    0.000050  0.000020  0.048724  0.053524  0.039410      ips       True   
21    0.000064  0.000017  0.052682  0.054296  0.039511      ips       True   
22    0.000031  0.000018  0.026421  0.054380  0.039333      ips       True   
23    0.000025  0.000010  0.029895  0.053392  0.039300      ips       True   
24    0.000011  0.000010  0.021288  0.058637  0.030177      ips       True   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
14          True         False  0.025682   0.012754  0.319129  0.827024  
17          True         False  0.022780   0.009134  0.236082  0.789834  
18          True         False  0.020788   0.008952  0.228107  0.784868  
20          True         False  0.021481   0.009381  0.246278  0.795654  
21          True         False  0.021395   0.009619  0.248381  0.795285  
22          True         False  0.025725   0.010273  0.273502  0.811475  
23          True         False  0.022824   0.010307  0.275221  0.817127  
24          True         False  0.024773   0.010333  0.275284  0.813982

## посмотрит на результаты при обучении на popular

In [13]:
df = pd.read_csv("results/dlce_on_popular_CO.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.02]

trial_id dataset     value  dim_factor             metric  learn_rate  \
12        12      CO  0.846149         244    upper_bound_log    0.005743   
14        14      CO  0.844321         232    upper_bound_log    0.005975   
20        20      CO  0.833430         152    upper_bound_log    0.008252   
22        22      CO  0.843588         227  upper_bound_hinge    0.003753   
24        24      CO  0.837188         247    upper_bound_log    0.003342   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
12    0.000084  0.000221  0.019906  0.023467  0.044587      ips      False   
14    0.000127  0.000185  0.011748  0.010460  0.058599      ips      False   
20    0.000039  0.000141  0.064689  0.017318  0.052805      ips      False   
22    0.000089  0.000478  0.010491  0.020734  0.040483      ips      False   
24    0.000047  0.000235  0.049422  0.026835  0.049172      ips      False   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
12          True         False  0.022867   0.014439  0.333361  0.846149  
14          True         False  0.022477   0.014045  0.325543  0.844321  
20          True         False  0.020355   0.014136  0.315780  0.833430  
22          True         False  0.024123   0.014149  0.326640  0.843588  
24          True         False  0.020355   0.014218  0.321564  0.837188

In [28]:
df = pd.read_csv("results/dlce_on_popular_CP.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.075]

trial_id dataset     value  dim_factor           metric  learn_rate  \
5          5      CP  1.186878         232  upper_bound_log    0.004106   
22        22      CP  1.178379         123  upper_bound_log    0.006771   
23        23      CP  1.183014         130  upper_bound_log    0.007753   
24        24      CP  1.160661         111  upper_bound_log    0.006778   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
5     0.000027  0.000056  0.019078  0.042306  0.015351      ips       True   
22    0.000119  0.000032  0.027656  0.043472  0.010786      ips       True   
23    0.000135  0.000046  0.024531  0.040657  0.006759      ips       True   
24    0.000135  0.000060  0.036620  0.039707  0.006915      ips       True   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
5           True         False  0.081767   0.024994  0.792853  1.186878  
22          True         False  0.079991   0.025665  0.792282  1.178379  
23          True         False  0.080338   0.025219  0.790627  1.183014  
24          True         False  0.075747   0.025037  0.766255  1.160661

## посмотрит на результаты при обучении на PropCare

In [30]:
df = pd.read_csv("results/dlce_on_propcare_CO.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.015]

trial_id dataset     value  dim_factor           metric  learn_rate  \
6          6      CO  0.830082         133  upper_bound_log    0.015574   
13        13      CO  0.836888         118  upper_bound_log    0.005248   
15        15      CO  0.842566         148  upper_bound_log    0.004981   
17        17      CO  0.851228         242  upper_bound_log    0.004507   
18        18      CO  0.837687         255  upper_bound_log    0.001876   
21        21      CO  0.836194         255  upper_bound_log    0.001737   
24        24      CO  0.851269         218  upper_bound_log    0.004576   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
6     0.000206  0.000016  0.090804  0.032789  0.042462      ips       True   
13    0.000102  0.000259  0.080417  0.010011  0.059891      ips       True   
15    0.000074  0.000031  0.066967  0.023951  0.018996      ips       True   
17    0.000027  0.000121  0.012391  0.013611  0.003128      ips       True   
18    0.000029  0.000107  0.012531  0.025902  0.001497      ips       True   
21    0.000037  0.000127  0.013745  0.024372  0.001615      ips       True   
24    0.000087  0.000034  0.045900  0.014102  0.023599      ips       True   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
6           True         False  0.015721   0.013300  0.287211  0.830082  
13          True         False  0.018146   0.013118  0.289930  0.836888  
15          True         False  0.015071   0.013543  0.302157  0.842566  
17          True         False  0.020615   0.014054  0.316388  0.851228  
18          True         False  0.020312   0.012139  0.277607  0.837687  
21          True         False  0.020961   0.012105  0.275775  0.836194  
24          True         False  0.019229   0.014807  0.327522  0.851269

In [33]:
df = pd.read_csv("results/dlce_on_propcare_CP.csv")
best_CO = df.loc[[df['CPrec_10'].idxmax()]].to_dict()
df[df['CPrec_10'] >= 0.07]

trial_id dataset     value  dim_factor           metric  learn_rate  \
0          0      CP  1.166110         246  upper_bound_log    0.007575   
11        11      CP  1.166642         255  upper_bound_log    0.003062   
12        12      CP  1.182451         252  upper_bound_log    0.005399   
16        16      CP  1.162040         194  upper_bound_log    0.005474   
20        20      CP  1.136230         210  upper_bound_log    0.006016   
21        21      CP  1.153788         241  upper_bound_log    0.006582   
22        22      CP  1.140373         241  upper_bound_log    0.008401   
24        24      CP  1.197898         227  upper_bound_log    0.004090   

    reg_factor  reg_bias     omega        xT        xC tau_mode  with_bias  \
0     0.002177  0.000300  0.047297  0.042740  0.051182      ips      False   
11    0.000131  0.000084  0.057982  0.043877  0.019791      ips       True   
12    0.000095  0.000139  0.044812  0.042952  0.020757      ips       True   
16    0.000165  0.000088  0.068298  0.037641  0.013471      ips       True   
20    0.000054  0.000133  0.079783  0.050868  0.002489      ips       True   
21    0.001879  0.000265  0.036427  0.042176  0.044930      ips      False   
22    0.001591  0.000260  0.052075  0.037746  0.032172      ips      False   
24    0.000120  0.000131  0.023975  0.040662  0.059784      ips      False   

    with_outcome  only_treated  CPrec_10  CPrec_100  CDCG_100      CDCG  
0           True         False  0.074881   0.028476  0.796949  1.166110  
11          True         False  0.075747   0.028662  0.800694  1.166642  
12          True         False  0.077306   0.030026  0.836352  1.182451  
16          True         False  0.076527   0.029121  0.803701  1.162040  
20          True         False  0.071893   0.029792  0.787521  1.136230  
21          True         False  0.074578   0.027592  0.772935  1.153788  
22          True         False  0.074361   0.029168  0.782392  1.140373  
24          True         False  0.079472   0.029220  0.840216  1.197898

## Теперь запустим лучшие модели по 5 раз

In [38]:
for prop_mode in ['random', 'popular', 'propcare']:
    for dataset in DATASETS:
        train_df, vali_df, test_df, num_users, num_items, _ = get_dataset(dataset, "./")
        
        if prop_mode == 'original':
            pass
        elif prop_mode == 'random':
            rd = RandomBase(num_users, num_items)
            rd.fit(train_df)
            train_df['propensity'] = rd.predict(train_df)
            vali_df['propensity'] = rd.predict(vali_df)

            train_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), train_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
            vali_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), vali_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
        elif prop_mode == 'popular':
            pop = PopularBase(num_users, num_items)
            pop.fit(train_df)
            train_df['propensity'] = pop.predict(train_df)
            vali_df['propensity'] = pop.predict(vali_df)

            train_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), train_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
            vali_df['treated'] = predict_z(train_df.rename(columns={'propensity' : 'pred'}), vali_df.rename(columns={'propensity' : 'pred'}), epsilon=0.2)
        elif prop_mode == 'propcare':
            propcare = PropCare.load_model(dir_path=f"saved_models/propcare/best_{dataset}", model_name=f"model_1", device='cuda')
            
            train_df['propensity'] = propcare.predict(train_df)
            vali_df['propensity'] = propcare.predict(vali_df)

            train_df['treated'] =  propcare.predict_z(train_df)
            vali_df['treated'] = propcare.predict_z(vali_df)
        else:
            raise NotImplementedError


        df = pd.read_csv(f"results/dlce_on_{prop_mode}_{dataset}.csv")
        best_params = df.iloc[[df['CPrec_10'].idxmax()]].squeeze().to_dict()

        for i in range(len(seeds)):
            model = DLCE(
                num_users=num_users,
                num_items=num_items,
                dim_factor=int(best_params['dim_factor']),
                metric=best_params['metric'],
                learn_rate=best_params['learn_rate'],
                reg_factor=best_params['reg_factor'],
                reg_bias=best_params['reg_bias'],
                omega=best_params['omega'],
                xT=best_params['xT'],
                xC=best_params['xC'],
                tau_mode=best_params['tau_mode'],
                with_bias=bool(best_params['with_bias']),
                with_outcome=bool(best_params['with_outcome']),
                only_treated=bool(best_params['only_treated']),
                device='cuda',
                seed = seeds[i]
            )

            # Обучаем модель
            model.fit(train_df, vali_df, n_epochs=40, batch_size=512)

            model.save_model(dir_path=f"saved_models/dlce/best_{prop_mode}_{dataset}", model_name=f"model_{i+1}")


DLCE:   2%|▉                                     | 1/40 [00:06<03:57,  6.09s/it]

Epoch 1/40, Train Loss: 172.6247, Validation Metrics: {'CPrec_10': np.float64(0.005283672585534863), 'CPrec_100': np.float64(0.004824599393676916), 'CDCG_100': 0.10368868542785288, 'CDCG': 0.7071660640756033}


DLCE:   5%|█▉                                    | 2/40 [00:12<04:08,  6.54s/it]

Epoch 2/40, Train Loss: 163.9146, Validation Metrics: {'CPrec_10': np.float64(0.009051537462104808), 'CPrec_100': np.float64(0.005881333910783889), 'CDCG_100': 0.13294175825325744, 'CDCG': 0.7231707565069944}


DLCE:   8%|██▊                                   | 3/40 [00:22<04:54,  7.96s/it]

...

DLCE:  95%|███████████████████████████████████▏ | 38/40 [04:45<00:15,  7.54s/it]

Epoch 38/40, Train Loss: 852.1638, Validation Metrics: {'CPrec_10': np.float64(0.08601126028583803), 'CPrec_100': np.float64(0.030025985275010828), 'CDCG_100': 0.876473671272525, 'CDCG': 1.2217401200044289}


DLCE:  98%|████████████████████████████████████ | 39/40 [04:52<00:07,  7.36s/it]

Epoch 39/40, Train Loss: 843.5661, Validation Metrics: {'CPrec_10': np.float64(0.0873538328280641), 'CPrec_100': np.float64(0.030246860112602858), 'CDCG_100': 0.8852425097169456, 'CDCG': 1.2270549804684248}


Epoch 40/40, Train Loss: 834.5588, Validation Metrics: {'CPrec_10': np.float64(0.08852317020355133), 'CPrec_100': np.float64(0.030225205716760503), 'CDCG_100': 0.8804191562496082, 'CDCG': 1.2227680465970827}
Model saved to: saved_models/dlce/best_propcare_CP/model_5


# DLCE c модификациями - CISP, naive, DLTO

In [8]:
for dlto_mode in [True, False]:
    for tau_mode in ['ips', 'cips', 'naive']:
        for dataset in DATASETS:
            train_df, vali_df, test_df, num_users, num_items, _ = get_dataset(dataset, "./")

            df = pd.read_csv(f"results/dlce_optuna_{dataset}.csv")
            best_params = df.iloc[[df['CPrec_10'].idxmax()]].squeeze().to_dict()

            for i in range(len(seeds)):
                model = DLCE(
                    num_users=num_users,
                    num_items=num_items,
                    dim_factor=int(best_params['dim_factor']),
                    metric=best_params['metric'],
                    learn_rate=best_params['learn_rate'],
                    reg_factor=best_params['reg_factor'],
                    reg_bias=best_params['reg_bias'],
                    omega=best_params['omega'],
                    xT=0.005,
                    xC=0.005,
                    tau_mode=tau_mode,
                    with_bias=bool(best_params['with_bias']),
                    with_outcome=bool(best_params['with_outcome']),
                    only_treated=dlto_mode,
                    device='cuda',
                    seed = seeds[i]
                )

                # Обучаем модель
                model.fit(train_df, vali_df, n_epochs=40, batch_size=512)

                model.save_model(dir_path=f"saved_models/dlce/modes/dlto{dlto_mode}_{tau_mode}_{dataset}", model_name=f"model_{i+1}")


DLCE:   2%|▉                                     | 1/40 [00:03<02:23,  3.69s/it]

Epoch 1/40, Train Loss: 1389.2725, Validation Metrics: {'CPrec_10': np.float64(0.006019922044174967), 'CPrec_100': np.float64(0.004573408401905587), 'CDCG_100': 0.10419476573235466, 'CDCG': 0.7164093668656047}


DLCE:   5%|█▉                                    | 2/40 [00:07<02:12,  3.48s/it]

Epoch 2/40, Train Loss: 1309.3505, Validation Metrics: {'CPrec_10': np.float64(0.0071026418362927675), 'CPrec_100': np.float64(0.004902555218709398), 'CDCG_100': 0.11123973259605242, 'CDCG': 0.723097056945546}


DLCE:   8%|██▊                                   | 3/40 [00:10<02:04,  3.36s/it]

...

DLCE:  95%|███████████████████████████████████▏ | 38/40 [04:21<00:13,  6.68s/it]

Epoch 38/40, Train Loss: 187.8164, Validation Metrics: {'CPrec_10': np.float64(0.07544391511476829), 'CPrec_100': np.float64(0.036721524469467304), 'CDCG_100': 0.9560823378678296, 'CDCG': 1.2622316082040876}


DLCE:  98%|████████████████████████████████████ | 39/40 [04:27<00:06,  6.55s/it]

Epoch 39/40, Train Loss: 187.0493, Validation Metrics: {'CPrec_10': np.float64(0.07739281074058034), 'CPrec_100': np.float64(0.03671286271113036), 'CDCG_100': 0.9379166811575286, 'CDCG': 1.2449291108755254}


Epoch 40/40, Train Loss: 187.0870, Validation Metrics: {'CPrec_10': np.float64(0.075790385448246), 'CPrec_100': np.float64(0.0370073624945864), 'CDCG_100': 0.9562956710316505, 'CDCG': 1.2577191105457242}
Model saved to: saved_models/dlce/modes/dltoFalse_naive_CP/model_5
